In [2]:
from torch import nn
from torch import optim
from torchvision import transforms
from torch.optim import lr_scheduler

In [3]:
from generate_c3d_model import generate_model
from train import train_epoch

In [4]:
from datasets.nv import NV

In [5]:
from utils import *
from target_transforms import *

In [6]:
from logger.logger import get_logger
logger = get_logger(__name__)

In [7]:
torch.manual_seed(1)

In [8]:
arch = '{}'.format('c3d')
n_epochs = 35
n_classes = 26
sample_size = 112
sample_duration = 10
ft_portion = "last_layer"
downsample = 2
scale_step = 0.84089641525
scales = [1.0]
for i in range(1, 5):
    scales.append(scales[-1] * scale_step)

In [10]:
model, parameters = generate_model(n_classes, sample_size, ft_portion)

generate_c3d_model 2024-03-02 10:58:00,066 INFO Torch version: 2.2.1
generate_c3d_model 2024-03-02 10:58:00,068 INFO Is CUDA enabled? True
generate_c3d_model 2024-03-02 10:58:00,565 INFO Total number of trainable parameters: 31913114
generate_c3d_model 2024-03-02 10:58:00,567 INFO  Converting the pretrained model to RGB+D init model
generate_c3d_model 2024-03-02 10:58:00,810 INFO  Done. RGB-D model ready.


last_layer


In [11]:
criterion = nn.CrossEntropyLoss()
criterion = criterion.cuda()
spatial_transform = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize([0, 0, 0], [1, 1, 1])
])
temporal_transform = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize([0, 0, 0], [1, 1, 1])])
target_transform = ClassLabel()
optimizer = optim.SGD(
    parameters,
    lr=0.1,
    momentum=0.9,
    dampening=0.9,
    weight_decay=1e-3,
    nesterov=False)

scheduler = lr_scheduler.ReduceLROnPlateau(
    optimizer, 'min', patience=10)

In [12]:
training_data = NV(
    './nvGesture_v1.1/nvGesture_v1',
    './annotation_nvGesture_v1/nvall_but_None.json',
    'training',
    spatial_transform=spatial_transform,
    temporal_transform=temporal_transform,
    target_transform=target_transform,
    sample_duration=sample_duration,
    modality="RGB-D")

FileNotFoundError: [Errno 2] No such file or directory: './annotation_nvGesture_v1/nvall_but_None.json'

In [ ]:
train_loader = torch.utils.data.DataLoader(
    training_data,
    batch_size=80,
    shuffle=True,
    num_workers=12,
    pin_memory=True)

In [ ]:
# logger.info(f"run")
# best_prec1 = 0
# for i in range(1, n_epochs + 1):
#     # for i in range(opt.begin_epoch, opt.begin_epoch + 10):
#     torch.cuda.empty_cache()
#     adjust_learning_rate(optimizer, i)
#     train_epoch(i, train_loader, model, criterion, optimizer)
#     state = {
#         'epoch': i,
#         'arch': arch,
#         'state_dict': model.state_dict(),
#         'optimizer': optimizer.state_dict(),
#         'best_prec1': best_prec1
#     }
#     save_checkpoint(state, False) 
#     

In [ ]:
if __name__ == '__main__':
    logger.info(f"run")
    best_prec1 = 0
    for i in range(1, n_epochs + 1):
        # for i in range(opt.begin_epoch, opt.begin_epoch + 10):
        torch.cuda.empty_cache()
        adjust_learning_rate(optimizer, i)
        train_epoch(i, train_loader, model, criterion, optimizer)
        state = {
            'epoch': i,
            'arch': arch,
            'state_dict': model.state_dict(),
            'optimizer': optimizer.state_dict(),
            'best_prec1': best_prec1
        }
        save_checkpoint(state, False) 
        